# Final Project
### Harmony of Nature: How Earthquake - Volcano Correlate

In [ ]:
import matplotlib.pyplot as plt 
import numpy as np
import obspy as op
import cartopy.crs as ccrs
from obspy.clients.fdsn import Client
import cartopy.feature as cfeature
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

import datetime
import matplotlib.dates as mdates
%matplotlib osx 
from matplotlib import cm
from matplotlib.widgets import TextBox


In [ ]:
'''Earthquake Data'''
currentDT = datetime.datetime.now()
print ('Download initiated. Should take about 8 seconds but requires an internet connection.')
print ('Download began: ',str(currentDT))

client = Client("IRIS")
t1 = op.UTCDateTime("2013-01-01T00:00:00") #start time of the request
t2 = op.UTCDateTime("2023-01-01T00:00:00") #end time of the request
minMag = 6.0
catalog = client.get_events(starttime=t1, endtime=t2, minmagnitude=minMag)

currentDT = datetime.datetime.now()
print ('Download ended: ',str(currentDT))

In [ ]:
'''Volcano Data'''
volc_file = np.loadtxt('GVP_Eruption_Results_modified_again_2013_2023.txt') # volcano file
print(volc_file)

In [ ]:
'''Asia'''
minLat = -50.508298
maxLat = 75.052433
minLon = 69.933152
maxLon = 178.917520
minMag = 6.0
catalog = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)

#print('Total number of EQ globally is {}'.format(len(catalog.events)))

In [ ]:
'''Volcano Data'''
lat_vol = [data[7] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]
long_vol = [data[8] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=5, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [ ]:
class volcano:
    def __init__(self, year, month, day, lat, long):
        self.year = year
        self.month = month
        self.day = day
        self.lat = lat
        self.long = long
        self.earthquakes = []
def toMonths(year, month, day):
    if month == 1 or 3 or 5 or 7 or 8 or 10 or 12:
        return (year*12) + month + (day/31)
    if month == 4 or 6 or 9 or 11:
        return (year*12) + month + (day/30)
    if month == 2:
         if year%4==0:
                 return(year*12)+month+(day/28)
         else:
                  return (year*12) + month + (day/29)

volc_file = np.loadtxt('GVP_Eruption_Results_modified_again_2013_2023.txt')
volcanoes = []
for i in volc_file:
    volcanoes.append(volcano(i[1], i[2], i[3], i[7], i[8]))

for i in catalog: 
    year = (int)(i.origins[0].time.year)
    month = (int)(i.origins[0].time.month)
    day = (int)(i.origins[0].time.day)
    lat1 = i.origins[0].latitude
    long1 = i.origins[0].longitude
    for j in volcanoes:
        lat2 = j.lat
        long2 = j.long
        y_diff = np.abs(lat1 - lat2) * 111.3
        avg_lat = np.abs((lat1+lat2)/2)
        x_diff = np.abs(long1-long2)*np.cos(np.radians(avg_lat))*111.3
        dist = np.sqrt(x_diff**2 + y_diff**2)
        if toMonths(j.year, j.month, j.day)-toMonths(year, month, day) < 5 and toMonths(j.year, j.month, j.day)-toMonths(year, month, day) > 0 and dist < 80: #months, km
            j.earthquakes.append(i)
#if caused is true then that volcano may have been caused by any of the earthquakes in volc.earthquakes
count = 0
num_volc = 0
for i in volcanoes:
   if i.year >= 2013:
       num_volc +=1
   if len(i.earthquakes) > 0:
       count +=1
        #the volcano was caused by an earthquake 

In [ ]:
print('Number of volcanoes =', num_volc)
print('Number of volcanoes caused by earthquakes =', count)
print('Correlation percentage = {}%'.format( count/num_volc * 100))

In [ ]:
def toformat(month):
    return (str)((month-1)//12) + "-" +(str) ((month-1)%12 +1)

In [ ]:
fig = plt.figure(figsize = (10,6))
    
with writer.saving(fig, "Asia.mp4", dpi=200):
    ax = fig.add_subplot(1,1,1,projection = ccrs.PlateCarree())
    ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
    ax.gridlines()
    import cartopy.io.img_tiles as cimgt
    request = cimgt.GoogleTiles()
    ax.add_feature(cfeature.BORDERS, linestyle=':')
    ax.add_image(request, 1)


    long = []
    lat = []
    vlat = []
    vlong = []
    evlong = []
    evlat = []


    for i in range(2013*12, 2023*12+1):
        for e in catalog:
            if toMonths(e.origins[0].time.year, e.origins[0].time.month, e.origins[0].time.day) // 1 == i:
                long.append(e.origins[0].longitude)
                lat.append(e.origins[0].latitude)
                ax.scatter(long, lat, c='b',s=40,transform=ccrs.PlateCarree())
        for v in volcanoes:
            if toMonths(v.year, v.month, v.day) // 1 == i:
                if len(v.earthquakes) > 0:
                    evlong.append(v.long)
                    evlat.append(v.lat)
                    ax.scatter(evlong, evlat, zorder=2,c='g',s=40,transform=ccrs.PlateCarree())
                else: 
                     vlong.append(v.long)
                     vlat.append(v.lat)
                     ax.scatter(vlong, vlat, zorder=1,c='r',s=40,transform=ccrs.PlateCarree())
        
        plt.title(toformat(i))
        plt.draw()
        plt.pause(0.1)
        writer.grab_frame()

In [ ]:
'''Europe & Africa'''
minLat = -40.707842
maxLat = 66.066809
minLon = -29.559032
maxLon = 75.291240
minMag = 6.0
catalog = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)

#print('Total number of EQ globally is {}'.format(len(catalog.events)))

In [ ]:
lat_vol = [data[7] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]
long_vol = [data[8] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]

In [ ]:
class volcano:
    def __init__(self, year, month, day, lat, long):
        self.year = year
        self.month = month
        self.day = day
        self.lat = lat
        self.long = long
        self.earthquakes = []
def toMonths(year, month, day):
    if month == 1 or 3 or 5 or 7 or 8 or 10 or 12:
        return (year*12) + month + (day/31)
    if month == 4 or 6 or 9 or 11:
        return (year*12) + month + (day/30)
    if month == 2:
         if year%4==0:
                 return(year*12)+month+(day/28)
         else:
                  return (year*12) + month + (day/29)

volc_file = np.loadtxt('GVP_Eruption_Results_modified_again_2013_2023.txt')
volcanoes = []
for i in volc_file:
    volcanoes.append(volcano(i[1], i[2], i[3], i[7], i[8]))

for i in catalog: 
    year = (int)(i.origins[0].time.year)
    month = (int)(i.origins[0].time.month)
    day = (int)(i.origins[0].time.day)
    lat1 = i.origins[0].latitude
    long1 = i.origins[0].longitude
    for j in volcanoes:
        lat2 = j.lat
        long2 = j.long
        y_diff = np.abs(lat1 - lat2) * 111.3
        avg_lat = np.abs((lat1+lat2)/2)
        x_diff = np.abs(long1-long2)*np.cos(np.radians(avg_lat))*111.3
        dist = np.sqrt(x_diff**2 + y_diff**2)
        if toMonths(j.year, j.month, j.day)-toMonths(year, month, day) < 5 and toMonths(j.year, j.month, j.day)-toMonths(year, month, day) > 0 and dist < 80: #months, km
            j.earthquakes.append(i)
#if caused is true then that volcano may have been caused by any of the earthquakes in volc.earthquakes
count = 0
num_volc = 0
for i in volcanoes:
   if i.year >= 2013:
       num_volc +=1
   if len(i.earthquakes) > 0:
       count +=1
        #the volcano was caused by an earthquake 

In [ ]:
print('Number of volcanoes =', num_volc)
print('Number of volcanoes caused by earthquakes =', count)
print('Correlation percentage = {}%'.format( count/num_volc * 100))

In [ ]:
def toformat(month):
    return (str)((month-1)//12) + "-" +(str) ((month-1)%12 +1)

fig = plt.figure(figsize = (10,6))
    
with writer.saving(fig, "Europe_Africa.mp4", dpi=200):
    ax = fig.add_subplot(1,1,1,projection = ccrs.PlateCarree())
    ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
    ax.gridlines()
    import cartopy.io.img_tiles as cimgt
    request = cimgt.GoogleTiles()
    ax.add_feature(cfeature.BORDERS, linestyle=':')
    ax.add_image(request, 1)


    long = []
    lat = []
    vlat = []
    vlong = []
    evlong = []
    evlat = []


    for i in range(2013*12, 2023*12+1):
        for e in catalog:
            if toMonths(e.origins[0].time.year, e.origins[0].time.month, e.origins[0].time.day) // 1 == i:
                long.append(e.origins[0].longitude)
                lat.append(e.origins[0].latitude)
                ax.scatter(long, lat, c='b',s=40,transform=ccrs.PlateCarree())
        for v in volcanoes:
            if toMonths(v.year, v.month, v.day) // 1 == i:
                if len(v.earthquakes) > 0:
                    evlong.append(v.long)
                    evlat.append(v.lat)
                    ax.scatter(evlong, evlat, zorder=2,c='g',s=40,transform=ccrs.PlateCarree())
                else: 
                     vlong.append(v.long)
                     vlat.append(v.lat)
                     ax.scatter(vlong, vlat, zorder=1,c='r',s=40,transform=ccrs.PlateCarree())
        plt.title(toformat(i))
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()

In [ ]:
'''North America & Greenland'''
minLat = 22.698453
maxLat = 83.650667
minLon = -161.745684
maxLon = -13.386317
minMag = 6.0
catalog = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)

#print('Total number of EQ globally is {}'.format(len(catalog.events)))

In [ ]:
lat_vol = [data[7] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]
long_vol = [data[8] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]

In [ ]:
class volcano:
    def __init__(self, year, month, day, lat, long):
        self.year = year
        self.month = month
        self.day = day
        self.lat = lat
        self.long = long
        self.earthquakes = []
def toMonths(year, month, day):
    if month == 1 or 3 or 5 or 7 or 8 or 10 or 12:
        return (year*12) + month + (day/31)
    if month == 4 or 6 or 9 or 11:
        return (year*12) + month + (day/30)
    if month == 2:
         if year%4==0:
                 return(year*12)+month+(day/28)
         else:
                  return (year*12) + month + (day/29)

volc_file = np.loadtxt('GVP_Eruption_Results_modified_again_2013_2023.txt')
volcanoes = []
for i in volc_file:
    volcanoes.append(volcano(i[1], i[2], i[3], i[7], i[8]))

for i in catalog: 
    year = (int)(i.origins[0].time.year)
    month = (int)(i.origins[0].time.month)
    day = (int)(i.origins[0].time.day)
    lat1 = i.origins[0].latitude
    long1 = i.origins[0].longitude
    for j in volcanoes:
        lat2 = j.lat
        long2 = j.long
        y_diff = np.abs(lat1 - lat2) * 111.3
        avg_lat = np.abs((lat1+lat2)/2)
        x_diff = np.abs(long1-long2)*np.cos(np.radians(avg_lat))*111.3
        dist = np.sqrt(x_diff**2 + y_diff**2)
        if toMonths(j.year, j.month, j.day)-toMonths(year, month, day) < 5 and toMonths(j.year, j.month, j.day)-toMonths(year, month, day) > 0 and dist < 80: #months, km
            j.earthquakes.append(i)
#if caused is true then that volcano may have been caused by any of the earthquakes in volc.earthquakes
count = 0
num_volc = 0
for i in volcanoes:
   if i.year >= 2013:
       num_volc +=1
   if len(i.earthquakes) > 0:
       count +=1
        #the volcano was caused by an earthquake 

In [ ]:
print('Number of volcanoes =', num_volc)
print('Number of volcanoes caused by earthquakes =', count)
print('Correlation percentage = {}%'.format( count/num_volc * 100))

In [ ]:
def toformat(month):
    return (str)((month-1)//12) + "-" +(str) ((month-1)%12 +1)

fig = plt.figure(figsize = (10,6))
    
with writer.saving(fig, "North_America_Greenland.mp4", dpi=200):
    ax = fig.add_subplot(1,1,1,projection = ccrs.PlateCarree())
    ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
    ax.gridlines()
    import cartopy.io.img_tiles as cimgt
    request = cimgt.GoogleTiles()
    ax.add_feature(cfeature.BORDERS, linestyle=':')
    ax.add_image(request, 1)


    long = []
    lat = []
    vlat = []
    vlong = []
    evlong = []
    evlat = []


    for i in range(2013*12, 2023*12+1):
        for e in catalog:
            if toMonths(e.origins[0].time.year, e.origins[0].time.month, e.origins[0].time.day) // 1 == i:
                long.append(e.origins[0].longitude)
                lat.append(e.origins[0].latitude)
                ax.scatter(long, lat,c='b',s=40,transform=ccrs.PlateCarree())
        for v in volcanoes:
            if toMonths(v.year, v.month, v.day) // 1 == i:
                if len(v.earthquakes) > 0:
                    evlong.append(v.long)
                    evlat.append(v.lat)
                    ax.scatter(evlong, evlat, zorder=2,c='g',s=40,transform=ccrs.PlateCarree())
                else: 
                     vlong.append(v.long)
                     vlat.append(v.lat)
                     ax.scatter(vlong, vlat, zorder=1,c='r',s=40,transform=ccrs.PlateCarree())
        plt.title(toformat(i))
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()

In [ ]:
'''South America'''
minLat = -58.388303
maxLat = 29.020907
minLon = -116.394124
maxLon = -32.722253
minMag = 6.0
catalog = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)

#print('Total number of EQ globally is {}'.format(len(catalog.events)))

In [ ]:
lat_vol = [data[7] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]
long_vol = [data[8] for data in volc_file if (minLat < data[7] < maxLat) and (minLon < data[8] < maxLon)]

In [ ]:
class volcano:
    def __init__(self, year, month, day, lat, long):
        self.year = year
        self.month = month
        self.day = day
        self.lat = lat
        self.long = long
        self.earthquakes = []
def toMonths(year, month, day):
    if month == 1 or 3 or 5 or 7 or 8 or 10 or 12:
        return (year*12) + month + (day/31)
    if month == 4 or 6 or 9 or 11:
        return (year*12) + month + (day/30)
    if month == 2:
         if year%4==0:
                 return(year*12)+month+(day/28)
         else:
                  return (year*12) + month + (day/29)

volc_file = np.loadtxt('GVP_Eruption_Results_modified_again_2013_2023.txt')
volcanoes = []
for i in volc_file:
    volcanoes.append(volcano(i[1], i[2], i[3], i[7], i[8]))

for i in catalog: 
    year = (int)(i.origins[0].time.year)
    month = (int)(i.origins[0].time.month)
    day = (int)(i.origins[0].time.day)
    lat1 = i.origins[0].latitude
    long1 = i.origins[0].longitude
    for j in volcanoes:
        lat2 = j.lat
        long2 = j.long
        y_diff = np.abs(lat1 - lat2) * 111.3
        avg_lat = np.abs((lat1+lat2)/2)
        x_diff = np.abs(long1-long2)*np.cos(np.radians(avg_lat))*111.3
        dist = np.sqrt(x_diff**2 + y_diff**2)
        if toMonths(j.year, j.month, j.day)-toMonths(year, month, day) < 5 and toMonths(j.year, j.month, j.day)-toMonths(year, month, day) > 0 and dist < 80: #months, km
            j.earthquakes.append(i)
#if caused is true then that volcano may have been caused by any of the earthquakes in volc.earthquakes
count = 0
num_volc = 0
for i in volcanoes:
   if i.year >= 2013:
       num_volc +=1
   if len(i.earthquakes) > 0:
       count +=1
        #the volcano was caused by an earthquake 

In [ ]:
print('Number of volcanoes =', num_volc)
print('Number of volcanoes caused by earthquakes =', count)
print('Correlation percentage = {}%'.format( count/num_volc * 100))

In [ ]:
def toformat(month):
    return (str)((month-1)//12) + "-" +(str) ((month-1)%12 +1)

fig = plt.figure(figsize = (10,6))
    
with writer.saving(fig, "South_America.mp4", dpi=200):
    ax = fig.add_subplot(1,1,1,projection = ccrs.PlateCarree())
    ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
    ax.gridlines()
    import cartopy.io.img_tiles as cimgt
    request = cimgt.GoogleTiles()
    ax.add_feature(cfeature.BORDERS, linestyle=':')
    ax.add_image(request, 1)


    long = []
    lat = []
    vlat = []
    vlong = []
    evlong = []
    evlat = []


    for i in range(2013*12, 2023*12+1):
        for e in catalog:
            if toMonths(e.origins[0].time.year, e.origins[0].time.month, e.origins[0].time.day) // 1 == i:
                long.append(e.origins[0].longitude)
                lat.append(e.origins[0].latitude)
                ax.scatter(long, lat,c='b',s=40,transform=ccrs.PlateCarree())
        for v in volcanoes:
            if toMonths(v.year, v.month, v.day) // 1 == i:
                if len(v.earthquakes) > 0:
                    evlong.append(v.long)
                    evlat.append(v.lat)
                    ax.scatter(evlong, evlat, zorder=2,c='g',s=40,transform=ccrs.PlateCarree())
                else: 
                     vlong.append(v.long)
                     vlat.append(v.lat)
                     ax.scatter(vlong, vlat, zorder=1,c='r',s=40,transform=ccrs.PlateCarree())
        plt.title(toformat(i))
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()